In [1]:
import folium
from bokeh.plotting import figure, save
from bokeh.models import ColumnDataSource, HoverTool, LogColorMapper
import geopandas as gp
import pysal as ps
from bokeh.palettes import RdYlBu11 as palette
from bokeh.models import LogColorMapper
import pandas as pd
import numpy as np

%matplotlib inline

C:\Users\ramu225\Anaconda3\lib\site-packages\pysal\model\spvcm\abstracts.py:10: UserWarning: The `dill` module is required to use the sqlite backend fully.
  from .sqlite import head_to_sql, start_sql


In [2]:
geo = gp.read_file('C:/Workspace/TNC-Demand-Model/Inputs/Census Shapefiles/Chicago Tracts/geo_export_558aad9f-98d8-4dd5-a6b1-c1730155d596.shp')
rh = pd.read_csv('C:/Workspace/TNC-Demand-Model/Outputs/2019_Weekday_Ridehail.csv',index_col = 0)
geo_area = gp.read_file('C:/Workspace/TNC-Demand-Model/Inputs/Census Shapefiles/Tracts/tl_2019_17_tract/tl_2019_17_tract.shp')


C:\Users\ramu225\Anaconda3\lib\site-packages\numpy\lib\arraysetops.py:580: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


In [3]:
geo_area['SQUARE_MILES_LAND'] = geo_area['ALAND']*3.86102e-7
geo_area['GEOID'] = geo_area.GEOID.astype(float)

In [4]:
rh['TOTAL_TRIPS'] = rh.PRIVATE_TRIPS + rh.SHARED_TRIPS

In [5]:
len(rh)

3208005

In [6]:
len(geo)

801

In [7]:
tods = rh.TOD.unique()

In [8]:
geo['geoid10'] = geo.geoid10.astype(float)

In [9]:
centroids = pd.read_csv('C:/Workspace/TNC-Demand-Model/otp/points.csv')
centroids = gp.GeoDataFrame(centroids)
centroids['GEOID']  = centroids['GEOID'].astype(float)

In [ ]:
import folumn

In [1]:
# Initialize the map: 
m = folium.Map([41.8781, -87.6298], zoom_start=11)

for tod in tods:
    print('Working on TOD ' + str(tod))
    rh_tod = rh[rh['TOD'] == tod]
    
    for tract in geo.geoid10:
        m = folium.Map([41.8781, -87.6298], zoom_start=11)
        
        folium.Marker([geo[geo['geoid10'] == tract].centroid.y, geo[geo['geoid10'] == tract].centroid.x] , tooltip='Origin').add_to(m)
        
        rh_tod_tract = rh_tod[rh_tod['ORIGIN'] == tract]
        #rh_tod_tract = rh_tod_tract.groupby(by = ['Pickup Census Tract','Dropoff Census Tract'], as_index = False).sum()
       
       # bins = np.quantile(rh_tod_tract['TOTAL_TRIPS'], [0, 0.25, 0.5, 0.75, 0.98, 1])
        
        # Add the color for the chloropleth:
        m.choropleth(
         geo_data=geo,
         name= str(tract),
         data=rh_tod_tract,
         columns = ['DESTINATION', 'TOTAL_TRIPS'],
         key_on='feature.properties.geoid10',
         fill_color='RdPu',
         fill_opacity=0.6,
         line_opacity=0.2,
         legend_name='Dropoff Totals from Origin',
         highlight = True
        )

        folium.LayerControl().add_to(m)

        m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Dropoff Ridehailing Maps/' + str(tod) + '/Tract_' + str(tract) + '.html')



NameError: name 'folium' is not defined

In [49]:
print('Working on Pickups')
m = folium.Map([41.8781, -87.6298], zoom_start=11)

for tod in tods:
    print('Working on TOD ' + str(tod))
    rh_tod = rh[rh['TOD'] == tod]
    
    for tract in geo.geoid10:
        print('Working on tract ' + str(tract))
        m = folium.Map([41.8781, -87.6298], zoom_start=11)
        folium.Marker([geo[geo['geoid10'] == tract].centroid.y, geo[geo['geoid10'] == tract].centroid.x], tooltip='Destination').add_to(m)

        rh_tod_tract = rh_tod[rh_tod['DESTINATION'] == tract]
        #rh_tod_tract = rh_tod_tract.groupby(by = 'Dropoff Census Tract', as_index = False).sum()
        rh_tod_tract['TOTAL_TRIPS'] = rh_tod_tract['TOTAL_TRIPS'].fillna(0)
       
    # need to come up with a better way to select out the census tracts that do not have not any pickups going to any other 
    # census tract... they miss up the bins
       # bins = np.quantile(rh_tod_tract['TOTAL_TRIPS'], [0, 0.25, 0.75, 0.9, 0.98, 1])

        
        # Add the color for the chloropleth:
        m.choropleth(
         geo_data=geo,
         name= str(tract),
         data= rh_tod_tract,
         columns = ['ORIGIN', 'TOTAL_TRIPS'],
         key_on='feature.properties.geoid10',
         fill_color='RdPu',
         fill_opacity=0.6,
         line_opacity=0.2,
         legend_name='Pickup Totals to Destination',
         highlight = True
        )

        folium.LayerControl().add_to(m)

        m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Pickup Ridehailing Maps/' + str(tod) + '/Tract_' + str(tract) + '.html')


Working on Pickups
Working on TOD 1
Working on tract 17031842400.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipyker

Working on tract 17031840300.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipyker

Working on tract 17031841100.0


...

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipyker

Working on tract 17031292200.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipyker

Working on tract 17031630900.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # This is added back by InteractiveShellApp.init_path()
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipyker

In [41]:
print('Working on Daily Pickups')
m = folium.Map([41.8781, -87.6298], zoom_start=11)



for tract in geo.geoid10:
    m = folium.Map([41.8781, -87.6298], zoom_start=11)
    folium.Marker([geo[geo['geoid10'] == tract].centroid.y, geo[geo['geoid10'] == tract].centroid.x], tooltip='Destination').add_to(m)

    rh_tract = rh[rh['DESTINATION'] == tract]
    rh_tract = rh_tract.groupby(by = ['ORIGIN','DESTINATION'], as_index = False).sum()

    bins = np.quantile(rh_tract['TOTAL_TRIPS'], [0,0.5,0.75,0.9,0.98,1])

    # Add the color for the chloropleth:
    m.choropleth(
     geo_data=geo,
     name= str(tract),
     data=rh_tract,
     columns = ['ORIGIN', 'TOTAL_TRIPS'],
     key_on='feature.properties.geoid10',
     fill_color='RdPu',
     fill_opacity=0.6,
     line_opacity=0.2,
     legend_name='Pickup Totals to Destination',
     highlight = True
    )


    
    folium.LayerControl().add_to(m)

    m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Pickup Ridehailing Maps/Daily/Tract_' + str(tract) + '.html')


Working on Daily Pickups


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

...

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geo

In [43]:
print('Working on Daily Dropoffs')
m = folium.Map([41.8781, -87.6298], zoom_start=11)

#had to leave out this census tract because there is no pickups from here.... only 4 dropoffs
pickup_geo = geo[geo['geoid10'] != 17031770902]

for tract in pickup_geo.geoid10:
    print('Working on Tract ' + str(tract))
    m = folium.Map([41.8781, -87.6298], zoom_start=11)
    folium.Marker([geo[geo['geoid10'] == tract].centroid.y, geo[geo['geoid10'] == tract].centroid.x], tooltip='Origin').add_to(m)

    rh_tract = rh[rh['ORIGIN'] == tract]
    rh_tract = rh_tract.groupby(by = ['ORIGIN','DESTINATION'], as_index = False).sum()
    
    bins = np.quantile(rh_tract['TOTAL_TRIPS'], [0,0.5,0.75,0.9,0.98,1])
    
    # Add the color for the chloropleth:
    m.choropleth(
     geo_data=geo,
     name= str(tract),
     data=rh_tract,
     columns = ['DESTINATION', 'TOTAL_TRIPS'],
     key_on='feature.properties.geoid10',
     fill_color='RdPu',
     fill_opacity=0.6,
     line_opacity=0.2,
     legend_name='Total Dropoffs from Origin',
     bins = bins,
     highlight = True
    )

    folium.LayerControl().add_to(m)

    m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Dropoff ridehailing Maps/Daily/Tract_' + str(tract) + '.html')


Working on Daily Dropoffs
Working on Tract 17031842400.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on Tract 17031840300.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on Tract 17031841100.0


...

C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on Tract 17031292200.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on Tract 17031630900.0


C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  # Remove the CWD from sys.path while we load stuff.
C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


In [16]:
print('Working on TOD Origin only Map')
m = folium.Map([41.8781, -87.6298], zoom_start=11, tiles='Stamen Toner')

rh_tod_origin_only = rh.groupby(by = ['ORIGIN','TOD'], as_index = False).sum()

for tod in tods:
    df = rh_tod_origin_only[rh_tod_origin_only['TOD'] == tod]
    m = folium.Map([41.8781, -87.6298], zoom_start=11, tiles = 'Stamen Toner')

    df = df.merge(geo_area[['GEOID', 'SQUARE_MILES_LAND']], how = 'left', left_on = 'ORIGIN', right_on = 'GEOID')
    df['TOTAL_TRIPS_PER_SQ_MILE'] = df['TOTAL_TRIPS']/df['SQUARE_MILES_LAND']
    
    bins = np.quantile(df['TOTAL_TRIPS_PER_SQ_MILE'], [0,0.5,0.75,0.98,1])
    print(bins)
    
    # Add a pickup choropleth for each tod
    m.choropleth(
     geo_data=geo,
     name= str(tod) + '_Origins',
     data=df,
     columns = ['ORIGIN', 'TOTAL_TRIPS_PER_SQ_MILE'],
     key_on='feature.properties.geoid10',
     fill_color='RdPu',
     fill_opacity=0.6,
     line_opacity=0.2,
     bins = bins,
     legend_name='Pickups per Square Mile',
     highlight = True)

    m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Pickup Ridehailing Maps/TOD ' + str(tod) + ' Origins Map.html')

    
m = folium.Map([41.8781, -87.6298], zoom_start=11,  tiles='Stamen Toner')
    
rh_origin_only = rh.groupby(by = 'ORIGIN', as_index = False).sum()

rh_origin_only = rh_origin_only.merge(geo_area[['GEOID', 'SQUARE_MILES_LAND']], how = 'left', left_on = 'ORIGIN', right_on = 'GEOID')
rh_origin_only['TOTAL_TRIPS_PER_SQ_MILE'] = rh_origin_only['TOTAL_TRIPS']/rh_origin_only['SQUARE_MILES_LAND']

bins = np.quantile(rh_origin_only['TOTAL_TRIPS_PER_SQ_MILE'], [0,0.5,0.75,0.98,1])
print(bins)

# Add a origin choropleth for daily total
m.choropleth(
 geo_data=geo,
 name= 'Daily_Origins',
 data=rh_origin_only,
 columns = ['ORIGIN', 'TOTAL_TRIPS_PER_SQ_MILE'],
 key_on='feature.properties.geoid10',
 fill_color='RdPu',
 fill_opacity=0.6,
 line_opacity=0.2,
 bins = bins,
 legend_name='Pickups per Square Mile',
 highlight = True
)

feature_group = folium.FeatureGroup(name='Census Tract Centroids', show = False)

for tract2 in centroids.GEOID:
    row = centroids[centroids['GEOID'] == tract2]
    folium.CircleMarker([row['Y'], row['X']], popup = str(int(row['GEOID'].values[0])), radius = 1, fill = True, fill_color = 'grey', color = 'grey').add_to(feature_group)

m.add_child(feature_group)

    
folium.LayerControl().add_to(m)

m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Pickup Ridehailing Maps/Origins Daily Map.html')

print('Everything is Complete')


Working on TOD Origin only Map
[    0.           522.39955005  1927.47979274  7886.79688226
 21881.63810374]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


[   0.          114.92476441  298.17937067 1220.35149522 2596.72090929]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


[   0.          515.73691804 1138.8858585  3941.41624005 8339.3421561 ]


...

[   0.          286.1776051   715.3543588  2685.97993032 5003.80687632]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


[    0.           527.12298362  1277.02685201  4811.78996854
 10788.1185435 ]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


[    0.          2015.63276855  5224.67960456 19801.59270765
 47514.07349958]
Everything is Complete


In [17]:
print('Working on Destinations only Maps!')

m = folium.Map([41.8781, -87.6298], zoom_start=11,  tiles='Stamen Toner')

rh_tod_dest_only = rh.groupby(by = ['DESTINATION','TOD'], as_index = False).sum()

rh_tod_dest_only = rh_tod_dest_only.merge(geo_area[['GEOID', 'SQUARE_MILES_LAND']], how = 'left', left_on = 'DESTINATION', right_on = 'GEOID')
rh_tod_dest_only['TOTAL_TRIPS_PER_SQ_MILE'] = rh_tod_dest_only['TOTAL_TRIPS']/rh_tod_dest_only['SQUARE_MILES_LAND']

for tod in tods:
    print('Working on TOD ' + str(tod))
    df = rh_tod_dest_only[rh_tod_dest_only['TOD'] == tod]
    
    m = folium.Map([41.8781, -87.6298], zoom_start=11, tiles = 'Stamen Toner')

    #bins = np.linspace(min(df['TOTAL_TRIPS_PER_SQ_MILE']),max(df['TOTAL_TRIPS_PER_SQ_MILE']),9)
    bins = np.quantile(df['TOTAL_TRIPS_PER_SQ_MILE'], [0,0.5, 0.75,0.98,1])
    print(bins)
    # Add a dropoff choropleth for each tod
    m.choropleth(
     geo_data=geo,
     name= str(tod) + '_Destinations',
     data=df,
     columns = ['DESTINATION', 'TOTAL_TRIPS_PER_SQ_MILE'],
     key_on='feature.properties.geoid10',
     fill_color='RdPu',
     fill_opacity=0.6,
     line_opacity=0.2,
     bins = bins,
     legend_name='Dropoffs per Square Mile',
     highlight = True
    )

    m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Dropoff Ridehailing Maps/TOD ' + str(tod) + ' Destinations Map.html')

rh_dest_only = rh.groupby(by = 'DESTINATION', as_index = False).sum()

rh_dest_only = rh_dest_only.merge(geo_area[['GEOID', 'SQUARE_MILES_LAND']], how = 'left', left_on = 'DESTINATION', right_on = 'GEOID')

rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE'] = rh_dest_only['TOTAL_TRIPS']/rh_dest_only['SQUARE_MILES_LAND']


m = folium.Map([41.8781, -87.6298], zoom_start=11,  tiles='Stamen Toner')

#bins = np.linspace(min(rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE']),max(rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE']),0)
bins = np.quantile(rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE'], [0,0.5,0.75,0.98,1])
print(bins)

# Add a dropoff choropleth for daily total
m.choropleth(
 geo_data=geo,
 name= 'Daily_Destinations',
 data=rh_dest_only,
 columns = ['DESTINATION', 'TOTAL_TRIPS_PER_SQ_MILE'],
 key_on='feature.properties.geoid10',
 fill_color='RdPu',
 fill_opacity=0.6,
 line_opacity=0.2,
 bins = bins,
 legend_name='Dropoffs per Square Mile',
 highlight = True
)

feature_group = folium.FeatureGroup(name='Census Tract Centroids', show = False)

for tract2 in centroids.GEOID:
    row = centroids[centroids['GEOID'] == tract2]
    folium.CircleMarker([row['Y'], row['X']], popup = str(int(row['GEOID'].values[0])), radius = 1, fill = True, fill_color = 'grey', color = 'grey').add_to(feature_group)

m.add_child(feature_group)

folium.LayerControl().add_to(m)

m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Dropoff Ridehailing Maps/Destinations Daily Map.html')

print('Everything is Complete!')

Working on Destinations only Maps!
Working on TOD 1
[    0.           657.30403985  1965.9293866   8209.1432319
 16845.95369785]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on TOD 2
[   0.           26.7027695   141.79995098 1721.05719154 5772.81168146]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on TOD 3
[    0.           301.854751     808.70853261  4047.54358656
 10991.21434361]


...

Working on TOD 4
[   0.          166.27815079  494.03248472 3010.15040502 7116.12578196]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Working on TOD 5
[    0.           447.27339228  1149.05643798  4785.24575165
 12128.34473154]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


[    0.          1675.14792303  4611.70546551 22195.11216354
 50035.19753378]
Everything is Complete!


In [20]:
rh_all = rh_origin_only[['TOTAL_TRIPS_PER_SQ_MILE','ORIGIN']].merge(rh_dest_only[['TOTAL_TRIPS_PER_SQ_MILE','DESTINATION']], left_on = 'ORIGIN', right_on = 'DESTINATION', suffixes = ('_ORIGIN', '_DESTINATION'))

In [21]:
rh_all.head()

TOTAL_TRIPS_PER_SQ_MILE_ORIGIN        ORIGIN  \
0                     4144.772892  1.703101e+10   
1                     4051.194677  1.703101e+10   
2                     4388.476208  1.703101e+10   
3                     4372.849784  1.703101e+10   
4                     4051.458578  1.703101e+10   

   TOTAL_TRIPS_PER_SQ_MILE_DESTINATION   DESTINATION  
0                          3529.430344  1.703101e+10  
1                          2864.840249  1.703101e+10  
2                          4101.558368  1.703101e+10  
3                          3417.607999  1.703101e+10  
4                          5025.956525  1.703101e+10

In [22]:
len(rh_all)

801

In [23]:
rh_all['TOTAL_TRIPS_PER_SQ_MILE'] = rh_all.TOTAL_TRIPS_PER_SQ_MILE_ORIGIN + rh_all.TOTAL_TRIPS_PER_SQ_MILE_DESTINATION

In [25]:
rh_all.ORIGIN

0      1.703101e+10
1      1.703101e+10
2      1.703101e+10
3      1.703101e+10
4      1.703101e+10
           ...     
796    1.703184e+10
797    1.703184e+10
798    1.703184e+10
799    1.703198e+10
800    1.703198e+10
Name: ORIGIN, Length: 801, dtype: float64

In [28]:
m = folium.Map([41.8781, -87.6298], zoom_start=11,  tiles='Stamen Toner')

#bins = np.linspace(min(rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE']),max(rh_dest_only['TOTAL_TRIPS_PER_SQ_MILE']),0)
bins = np.quantile(rh_all['TOTAL_TRIPS_PER_SQ_MILE'], [0,0.5,0.75,0.98,1])
print(bins.astype(int))

# Add a dropoff choropleth for daily total
m.choropleth(
 geo_data=geo,
 name= 'Daily Pickup and Dropoff Totals',
 data=rh_all,
 columns = ['ORIGIN', 'TOTAL_TRIPS_PER_SQ_MILE'],
 key_on='feature.properties.geoid10',
 fill_color='RdPu',
 fill_opacity=0.6,
 line_opacity=0.2,
 bins = bins,
 legend_name='Pickups and Dropoffs per Square Mile',
 highlight = True
)

feature_group = folium.FeatureGroup(name='Census Tract Centroids', show = False)

for tract2 in centroids.GEOID:
    row = centroids[centroids['GEOID'] == tract2]
    folium.CircleMarker([row['Y'], row['X']], popup = str(int(row['GEOID'].values[0])), radius = 1, fill = True, fill_color = 'grey', color = 'grey').add_to(feature_group)

m.add_child(feature_group)

folium.LayerControl().add_to(m)

m.save('C:/Workspace/TNC-Demand-Model/Data Exploration/Ride-Hailing Daily Map.html')

print('Everything is Complete!')

[    5  3687  9885 40692 97549]


C:\Users\ramu225\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


Everything is Complete!
